# 8.0. Data Enrichment - Data Deduplication Summaries

In [1]:
from datetime import datetime
import os
import time
import pandas as pd 
import requests
import urllib3
import json
import sys
import numpy as np

pd.options.display.max_colwidth = 1000
pd.set_option('display.max_columns', None)

In [2]:
file = r'C:\Users\leona\OneDrive\Desktop\Tesi\Pipeline\Datasets\Pipeline\DataWrangling\Entries.csv'

In [3]:
df = pd.read_csv(file, low_memory = False)
df

Unnamed: 0   ID_ENTRY                 first_seen  \
0               0  2711900.0  2023-09-15 15:17:09+00:00   
1               1  2711899.0  2023-09-15 15:11:08+00:00   
2               2  2711898.0  2023-09-15 15:03:04+00:00   
3               3  2711897.0  2023-09-15 13:35:07+00:00   
4               4  2711896.0  2023-09-15 13:33:07+00:00   
...           ...        ...                        ...   
16594       15580        0.0  2023-08-24 23:29:43+00:00   
16595       15581        0.0  2023-08-25 01:29:36+00:00   
16596       15582        0.0  2023-08-25 10:08:52+00:00   
16597       15583        0.0  2023-08-25 11:24:40+00:00   
16598       15584        0.0  2023-08-25 15:24:34+00:00   

                                                                                                                             ioc  \
0                                                                                                     http://1.32.53.97:45188/.i   
1                                                                             https://kld.workout.oystergardener.net/editContent   
2                                                                                            http://178.141.204.195:38244/Mozi.m   
3                                                                          https://github.com/hoter666/8888/blob/main/Banana.exe   
4      http://mail.treeoflifeadventures.com/wp-content/plugins/70d5e28f51c1438d94e3e6dc84b95311/xt/mmd/shell/UMLrjk2KC4fpJg5.exe   
...                                                                                                                          ...   
16594                                                                                                             41.97.47.7:443   
16595                                                                                                           92.9.44.234:2222   
16596                                                                                                         78.152.198.132:443   
16597                                                                                                         113.193.95.229:443   
16598                                                                                                         190.34.24.159:2222   

        status                  last_seen       threat_type  \
0       online  2023-09-15 15:17:09+00:00  payload_delivery   
1      offline  2023-09-15 15:11:08+00:00  payload_delivery   
2      offline  2023-09-15 15:03:04+00:00  payload_delivery   
3       online  2023-09-15 15:04:29+00:00  payload_delivery   
4      offline  2023-09-15 13:56:00+00:00  payload_delivery   
...        ...                        ...               ...   
16594  offline  2023-08-25 00:00:00+00:00  payload_delivery   
16595  offline  2023-08-25 00:00:00+00:00  payload_delivery   
16596  offline  2023-08-25 00:00:00+00:00  payload_delivery   
16597  offline  2023-08-25 00:00:00+00:00  payload_delivery   
16598  offline  2023-08-25 00:00:00+00:00  payload_delivery   

                                   reference         reporter         source  \
0      https://urlhaus.abuse.ch/url/2711900/         geenensp       URL Haus   
1      https://urlhaus.abuse.ch/url/2711899/    Cryptolaemus1       URL Haus   
2      https://urlhaus.abuse.ch/url/2711898/       Gandylyan1       URL Haus   
3      https://urlhaus.abuse.ch/url/2711897/      Casperinous       URL Haus   
4      https://urlhaus.abuse.ch/url/2711896/  James_inthe_box       URL Haus   
...                                      ...              ...            ...   
16594         https://feodotracker.abuse.ch/    Feodo Tracker  Feodo Tracker   
16595         https://feodotracker.abuse.ch/    Feodo Tracker  Feodo Tracker   
16596         https://feodotracker.abuse.ch/    Feodo Tracker  Feodo Tracker   
16597         https://feodotracker.abuse.ch/    Feodo Tracker  Feodo Tracker   
16598         https://feodotracker.abuse.ch/    Feodo Tracker  Feodo Tracker

# Examine ioc fiield and perform Data Deduplication over it

In [4]:
def find_duplicates(input_list):
    seen = {}
    duplicates = []
    for item in input_list:
        if item in seen:
            duplicates.append(item)
        else:
            seen[item] = 1
    return duplicates

## Ioc Type : 'md5_hash', 'sha256_hash'

In [5]:
df['ioc_type'].unique()

array(['url', 'ip:port', 'domain', 'md5_hash', 'sha256_hash'],
      dtype=object)

In [6]:
files = df[((df['ioc'].notna()) & ((df['ioc_type'] == 'md5_hash') | (df['ioc_type'] == 'sha256_hash')))]
files 

Unnamed: 0   ID_ENTRY                 first_seen  \
7123         7123  1163775.0  2023-09-15 06:16:00+00:00   
7125         7125  1163774.0  2023-09-15 06:15:59+00:00   
7130         7130  1163784.0  2023-09-15 06:15:51+00:00   
7132         7132  1163783.0  2023-09-15 06:15:50+00:00   
7133         7133  1163780.0  2023-09-15 06:15:49+00:00   
7135         7135  1163779.0  2023-09-15 06:15:48+00:00   
7138         7138  1163790.0  2023-09-15 06:15:45+00:00   
7139         7139  1163791.0  2023-09-15 06:15:45+00:00   
7473         7473  1163443.0  2023-09-13 15:43:07+00:00   
8250         8250  1162670.0  2023-09-11 09:02:07+00:00   
8324         8324  1156052.0  2023-09-11 06:45:40+00:00   
8325         8325  1156053.0  2023-09-11 06:45:40+00:00   
15043       15043  1155823.0  2023-09-09 17:37:10+00:00   
15044       15044  1155824.0  2023-09-09 17:37:09+00:00   
15213       15213  1155686.0  2023-09-08 19:25:31+00:00   
15222       15222  1155687.0  2023-09-08 19:25:25+00:00   
15223       15223  1155688.0  2023-09-08 19:25:24+00:00   

                                                                    ioc  \
7123                                   7ca82baa3e7eddce41a25bf071216d1b   
7125   91a2d790366e433f18036a85d935d7e628c652c35b00427f6ef809fa9ec1f69e   
7130                                   c5521f937b54a93aaafd7ee393c8c598   
7132   18b60825348e063c719f443680ba8425dc968ad9cfb4f07f91fea89e2b2d1f0a   
7133                                   8b8d7db29e70be64c18a1cc8d02da680   
7135   be6716415c8f117ac0d290833825ac7ddab7f18666cd6e68218db31f3da357c2   
7138   91e5c5dbb6e64f5399cd4786f2e91192525b6582a088a8b583a7599a82838567   
7139                                   e9476ead29f19bde9b3d61f166e63aef   
7473                                   fd67ad03cc71d3397f962896365ed510   
8250                                   b556bd47157695e3e0b279d56401026f   
8324   2f53f658185eaa4ddcaf6e9ca529559a371b8720db09d53103cf6a9e9c0c3e2a   
8325                                   e52ef1f6efa8f51c077ffebc9e56b598   
15043  f403f15de411e46b588b0454694a868adf692ac5e7294d07bd3216d500971d3f   
15044                                  4f96080575bad35118f7639b75be224c   
15213  d27224eb9e5c34abfb22ba1941f3c4c4fbcfb5702899f8cf4fe280f4aa881d44   
15222  5a21b731fa6efbd890bcec79dc8ee32d38d78ff56ba4570b7edeef947b335484   
15223  77e02a67b7335161ae2abc3cd2a71540b75c78ab564cb3d993ae1e6dbcbeb615   

        status                  last_seen threat_type  \
7123   offline  2023-09-15 06:16:00+00:00     payload   
7125   offline  2023-09-15 06:15:59+00:00     payload   
7130   offline  2023-09-15 06:15:51+00:00     payload   
7132   offline  2023-09-14 23:45:29+00:00     payload   
7133   offline  2023-09-15 06:15:49+00:00     payload   
7135   offline  2023-09-15 06:15:48+00:00     payload   
7138   offline  2023-09-15 06:15:45+00:00     payload   
7139   offline  2023-09-15 06:15:45+00:00     payload   
7473   offline  2023-09-13 15:43:07+00:00     payload   
8250   offline  2023-09-11 09:02:07+00:00     payload   
8324   offline  2023-09-11 06:45:40+00:00     payload   
8325   offline  2023-09-11 06:45:40+00:00     payload   
15043  offline  2023-09-09 17:37:10+00:00     payload   
15044  offline  2023-09-09 17:37:09+00:00     payload   
15213  offline  2023-09-08 19:25:31+00:00     payload   
15222  offline  2023-09-08 19:25:25+00:00     payload   
15223  offline  2023-09-08 19:25:24+00:00     payload   

                                                             reference  \
7123        https://malpedia.caad.fkie.fraunhofer.de/details/apk.irata   
7125        https://malpedia.caad.fkie.fraunhofer.de/details/apk.irata   
7130        https://malpedia.caad.fkie.fraunhofer.de/details/apk.irata   
7132        https://malpedia.caad.fkie.fraunhofer.de/details/apk.irata   
7133        https://malpedia.caad.fkie.fraunhofer.de/details/apk.irata   
7135        https://malpedia.caad.fkie.fraunhofer.de/details/apk.irata   
7138        https://malpedia.caad.fkie.fraunhofe

In [7]:
dup_files = find_duplicates(files.ioc)
len(files)

17

# save FILES in a dataframes  

In [8]:
pd.DataFrame(files['ioc']).to_csv(r'C:\Users\leona\OneDrive\Desktop\Tesi\Pipeline\Datasets\Pipeline\BeforeCollection\files.csv')

### Summary

--> no duplicates in files

# Ioc Type : 'domain'

In [9]:
domains = df[(df['ioc'].notna()) & (df['ioc_type'] == 'domain')]
domains 

Unnamed: 0   ID_ENTRY                 first_seen                ioc  \
7060         7060  1163860.0  2023-09-15 12:17:36+00:00      7245.ddns.net   
7073         7073  1163838.0  2023-09-15 08:30:40+00:00       astrolco.fun   
7074         7074  1163839.0  2023-09-15 08:30:40+00:00     doggyguffy.fun   
7075         7075  1163840.0  2023-09-15 08:30:40+00:00       fartyfun.fun   
7076         7076  1163841.0  2023-09-15 08:30:39+00:00      fireworld.fun   
...           ...        ...                        ...                ...   
15221       15221  1155681.0  2023-09-08 19:25:26+00:00  amadapi.tuktuk.ug   
15224       15224  1155689.0  2023-09-08 19:25:24+00:00        stracer.top   
15225       15225  1155691.0  2023-09-08 19:25:24+00:00      kik.taybo.top   
15226       15226  1155690.0  2023-09-08 19:25:22+00:00          taybo.top   
15227       15227  1155692.0  2023-09-08 19:25:20+00:00    srk.stracer.top   

        status                  last_seen threat_type  \
7060   offline  2023-09-15 12:17:36+00:00      botnet   
7073   offline  2023-09-15 08:30:40+00:00      botnet   
7074   offline  2023-09-15 08:30:40+00:00      botnet   
7075   offline  2023-09-15 08:30:40+00:00      botnet   
7076   offline  2023-09-15 08:30:39+00:00      botnet   
...        ...                        ...         ...   
15221  offline  2023-09-09 10:14:48+00:00      botnet   
15224  offline  2023-09-08 19:25:24+00:00      botnet   
15225  offline  2023-09-08 19:25:24+00:00      botnet   
15226  offline  2023-09-08 19:25:22+00:00      botnet   
15227  offline  2023-09-08 19:25:20+00:00      botnet   

                                                                  reference  \
7060          https://malpedia.caad.fkie.fraunhofer.de/details/win.nanocore   
7073             https://malpedia.caad.fkie.fraunhofer.de/details/win.lumma   
7074             https://malpedia.caad.fkie.fraunhofer.de/details/win.lumma   
7075             https://malpedia.caad.fkie.fraunhofer.de/details/win.lumma   
7076             https://malpedia.caad.fkie.fraunhofer.de/details/win.lumma   
...                                                                     ...   
15221  https://malpedia.caad.fkie.fraunhofer.de/details/win.redline_stealer   
15224  https://malpedia.caad.fkie.fraunhofer.de/details/win.redline_stealer   
15225  https://malpedia.caad.fkie.fraunhofer.de/details/win.redline_stealer   
15226  https://malpedia.caad.fkie.fraunhofer.de/details/win.redline_stealer   
15227  https://malpedia.caad.fkie.fraunhofer.de/details/win.redline_stealer   

         reporter      source ioc_type          malware  
7060   SarlackLab  Threat Fox   domain         NanoCore  
7073       g0njxa  Threat Fox   domain    Lumma Stealer  
7074       g0njxa  Threat Fox   domain    Lumma Stealer  
7075       g0njxa  Threat Fox   domain    Lumma Stealer  
7076       g0njxa  Threat Fox   domain    Lumma Stealer  
...           ...         ...      ...              ...  
15221  SarlackLab  Threat Fox   domain            IRATA  
15224    500mk500  Threat Fox   domain  RedLine Stealer  
15225    500mk500  Threat Fox   domain  RedLine Stealer  
15226    500mk500  Threat Fox   domain  RedLine Stealer  
15227    500mk500  Threat Fox   domain  RedLine Stealer  

[4857 rows x 12 columns]

In [10]:
dup_domains = find_duplicates(domains.ioc)
dup_domains

['westwork-my.xyz',
 'many-verses.xyz',
 'fastcloudlife-my.xyz',
 'ollfiles-my.xyz',
 'dropfiles-my.xyz',
 'downloadfiles-my.xyz',
 'clonecloud-my.xyz',
 'diavellipromo-my.xyz',
 'skicloud-my.xyz',
 'vipmusic-my.xyz',
 'agustfreeday-my.xyz',
 'gstatic-node.io',
 'gapi-node.io',
 'blockall-my.xyz',
 'mycollection-my.xyz',
 'morevita-my.xyz',
 'coinflore-my.xyz',
 'gapi-node.io',
 'x10.bz']

In [11]:
unique_set = set(domains.ioc)

# Convert the set back to a list if needed
unique_list = list(unique_set)

unique_domains = pd.DataFrame()
unique_domains['ioc'] =  unique_list
unique_domains

ioc
0                       xeirz.ddns.net
1                    bbbr1.ddns.com.br
2                       proxy22.rt3.io
3          expresschiatto.freeddns.org
4                max-cleaner.at.ply.gg
...                                ...
4833                   iwantcheats.xyz
4834               mika201.duckdns.org
4835              craciton.duckdns.org
4836        babyboyhammer2.duckdns.org
4837  pedroalcantaralora09.duckdns.org

[4838 rows x 1 columns]

### Save values in a folder

In [12]:
unique_domains.to_csv(r'C:\Users\leona\OneDrive\Desktop\Tesi\Pipeline\Datasets\Pipeline\BeforeCollection\domains.csv')

## Summary for Domain

In [13]:
d = dup_domains[10]

df[df['ioc'] == d]

Unnamed: 0   ID_ENTRY                 first_seen                  ioc  \
7902        7902  1162966.0  2023-09-12 05:18:45+00:00  agustfreeday-my.xyz   
8037        8037  1162894.0  2023-09-11 17:51:04+00:00  agustfreeday-my.xyz   

       status                  last_seen threat_type  \
7902  offline  2023-09-12 05:18:45+00:00      botnet   
8037  offline  2023-09-11 17:51:04+00:00      botnet   

                                                       reference  reporter  \
7902  https://malpedia.caad.fkie.fraunhofer.de/details/win.lumma  500mk500   
8037  https://malpedia.caad.fkie.fraunhofer.de/details/win.lumma    1ZRR4H   

          source ioc_type        malware  
7902  Threat Fox   domain  Lumma Stealer  
8037  Threat Fox   domain  Lumma Stealer

In [14]:
tmp_df = df[df['ioc'] == dup_domains[10]]
tmp_df.reset_index( inplace=True)
s = pd.DataFrame(tmp_df.loc[1]).T
s

index Unnamed: 0   ID_ENTRY                 first_seen                  ioc  \
1  8037       8037  1162894.0  2023-09-11 17:51:04+00:00  agustfreeday-my.xyz   

    status                  last_seen threat_type  \
1  offline  2023-09-11 17:51:04+00:00      botnet   

                                                    reference reporter  \
1  https://malpedia.caad.fkie.fraunhofer.de/details/win.lumma   1ZRR4H   

       source ioc_type        malware  
1  Threat Fox   domain  Lumma Stealer

In [15]:
def create_summary_domain(dataframe, urls):
    
    summary = pd.DataFrame()

    for i in range(len(urls)):
                
        tmp_df = dataframe[dataframe['ioc'] == urls[i]]
                
        for j in range(len(tmp_df)):
            
            df = pd.DataFrame(tmp_df.iloc[j]).T
                        
            df.reset_index(drop=True, inplace=True)
                                            
            if(j == 0):
                
                max_first_seen = datetime.strptime(str(df.iloc[0]['first_seen']), '%Y-%m-%d %H:%M:%S%z')
                                
                max_last_seen = datetime.strptime(str(df.iloc[0]['last_seen']), '%Y-%m-%d %H:%M:%S%z')
                
                max_s = [str(df.iloc[0]['source'])]

                max_ioc = str(df.iloc[0]['ioc'])
            
                max_m = [str(df.iloc[0]['malware'])]
                
                r = str(df.iloc[0]['source']) + '.' + str(df.iloc[0]['reporter'])

                max_reporter = [r]
                
            else: 
                
                first_seen = datetime.strptime(str(df.iloc[0]['first_seen']), '%Y-%m-%d %H:%M:%S%z')
                
                date_difference = max_first_seen - first_seen
                previous_date = first_seen if date_difference.days > 0 else max_first_seen
                                
                last_seen = datetime.strptime(str(df.iloc[0]['last_seen']), '%Y-%m-%d %H:%M:%S%z')
                
                date_difference = max_last_seen - last_seen
                last_date = max_last_seen if date_difference.days > 0 else last_seen
                
                s = [str(df.iloc[0]['source'])]
                
                max_s = max_s if (s in max_s) else (max_s + s)
            
                m = [str(df.iloc[0]['malware'])]
                
                max_m = max_m if (m in max_m) else (max_m + m)
                
                r = [str(df.iloc[0]['source']) + '.' + str(df.iloc[0]['reporter'])]
                
                max_reporter = max_reporter if (r in  max_reporter) else (max_reporter + r )
                
        columns = ['ioc', 'first_seen', 'last_seen', 'source', 'malware', 'reporter']
             
        row = pd.DataFrame(columns=columns)
        row_values = [max_ioc, max_first_seen, max_last_seen, drop_duplicates(max_s), drop_duplicates(max_m), drop_duplicates(max_reporter)] 
        row.loc[0] = row_values            
        summary = pd.concat([summary, row]) 
                  
    return summary

In [16]:
def drop_duplicates(my_list):
    
    unique_list = []

# Iterate through the original list and add elements to unique_list only if they are not already present
    for item in my_list:
        if item not in unique_list:
            unique_list.append(item)
    if(len(unique_list) == 1):
        return unique_list[0]
    return unique_list

In [17]:
summary_domain = create_summary_domain(df, dup_domains)
summary_domain

ioc                first_seen                 last_seen  \
0       westwork-my.xyz 2023-09-12 05:19:09+00:00 2023-09-12 05:19:09+00:00   
0       many-verses.xyz 2023-09-12 05:19:09+00:00 2023-09-12 05:19:09+00:00   
0  fastcloudlife-my.xyz 2023-09-12 05:19:08+00:00 2023-09-12 05:19:08+00:00   
0       ollfiles-my.xyz 2023-09-12 05:19:08+00:00 2023-09-12 05:19:08+00:00   
0      dropfiles-my.xyz 2023-09-12 05:19:08+00:00 2023-09-12 05:19:08+00:00   
0  downloadfiles-my.xyz 2023-09-12 05:19:07+00:00 2023-09-12 05:19:07+00:00   
0     clonecloud-my.xyz 2023-09-12 05:18:52+00:00 2023-09-12 05:18:52+00:00   
0  diavellipromo-my.xyz 2023-09-12 05:18:51+00:00 2023-09-12 05:18:51+00:00   
0       skicloud-my.xyz 2023-09-12 05:18:50+00:00 2023-09-12 05:18:50+00:00   
0       vipmusic-my.xyz 2023-09-12 05:18:50+00:00 2023-09-12 05:18:50+00:00   
0   agustfreeday-my.xyz 2023-09-12 05:18:45+00:00 2023-09-12 05:18:45+00:00   
0       gstatic-node.io 2023-09-12 05:18:44+00:00 2023-09-12 05:18:44+00:00   
0          gapi-node.io 2023-09-12 05:19:11+00:00 2023-09-12 05:19:11+00:00   
0       blockall-my.xyz 2023-09-12 05:19:10+00:00 2023-09-12 05:19:10+00:00   
0   mycollection-my.xyz 2023-09-12 05:19:13+00:00 2023-09-12 05:19:13+00:00   
0       morevita-my.xyz 2023-09-12 05:19:13+00:00 2023-09-12 05:19:13+00:00   
0      coinflore-my.xyz 2023-09-12 05:19:12+00:00 2023-09-12 05:19:12+00:00   
0          gapi-node.io 2023-09-12 05:19:11+00:00 2023-09-12 05:19:11+00:00   
0                x10.bz 2023-09-11 06:45:42+00:00 2023-09-11 06:45:42+00:00   

       source        malware  \
0  Threat Fox  Lumma Stealer   
0  Threat Fox  Lumma Stealer   
0  Threat Fox  Lumma Stealer   
0  Threat Fox  Lumma Stealer   
0  Threat Fox  Lumma Stealer   
0  Threat Fox  Lumma Stealer   
0  Threat Fox  Lumma Stealer   
0  Threat Fox  Lumma Stealer   
0  Threat Fox  Lumma Stealer   
0  Threat Fox  Lumma Stealer   
0  Threat Fox  Lumma Stealer   
0  Threat Fox  Lumma Stealer   
0  Threat Fox  Lumma Stealer   
0  Threat Fox  Lumma Stealer   
0  Threat Fox  Lumma Stealer   
0  Threat Fox  Lumma Stealer   
0  Threat Fox  Lumma Stealer   
0  Threat Fox  Lumma Stealer   
0  Threat Fox          IRATA   

                                                        reporter  
0                       [Threat Fox.500mk500, Threat Fox.1ZRR4H]  
0                       [Threat Fox.500mk500, Threat Fox.1ZRR4H]  
0                       [Threat Fox.500mk500, Threat Fox.1ZRR4H]  
0                       [Threat Fox.500mk500, Threat Fox.1ZRR4H]  
0                       [Threat Fox.500mk500, Threat Fox.1ZRR4H]  
0                       [Threat Fox.500mk500, Threat Fox.1ZRR4H]  
0                       [Threat Fox.500mk500, Threat Fox.1ZRR4H]  
0                       [Threat Fox.500mk500, Threat Fox.1ZRR4H]  
0                       [Threat Fox.500mk500, Threat Fox.1ZRR4H]  
0                       [Threat Fox.500mk500, Threat Fox.1ZRR4H]  
0                       [Threat Fox.500mk500, Threat Fox.1ZRR4H]  
0                       [Threat Fox.500mk500, Threat Fox.1ZRR4H]  
0  [Threat Fox.500mk500, Threat Fox.1ZRR4H, Threat Fox.abuse_ch]  
0                       [Threat Fox.500mk500, Threat Fox.1ZRR4H]  
0                       [Threat Fox.500mk500, Threat Fox.1ZRR4H]  
0                       [Threat Fox.500mk500, Threat Fox.1ZRR4H]  
0                       [Threat Fox.500mk500, Threat Fox.1ZRR4H]  
0  [Threat Fox.500mk500, Threat Fox.1ZRR4H, Threat Fox.abuse_ch]  
0                                          Threat Fox.onecert_ir

In [18]:
summary_domain.to_csv(r'C:\Users\leona\OneDrive\Desktop\Tesi\Pipeline\Datasets\Pipeline\Summary\domains.csv')

# Ioc Type : 'url'

In [19]:
urls = df[(df['ioc'].notna()) & (df['ioc_type'] == 'url')]
urls 

Unnamed: 0   ID_ENTRY                 first_seen  \
0               0  2711900.0  2023-09-15 15:17:09+00:00   
1               1  2711899.0  2023-09-15 15:11:08+00:00   
2               2  2711898.0  2023-09-15 15:03:04+00:00   
3               3  2711897.0  2023-09-15 13:35:07+00:00   
4               4  2711896.0  2023-09-15 13:33:07+00:00   
...           ...        ...                        ...   
15234       15234  1155704.0  2023-09-08 19:25:17+00:00   
15235       15235  1155710.0  2023-09-08 19:25:16+00:00   
15236       15236  1155711.0  2023-09-08 19:25:16+00:00   
15237       15237  1155712.0  2023-09-08 19:25:15+00:00   
15241       15241  1155706.0  2023-09-08 17:55:15+00:00   

                                                                                                                             ioc  \
0                                                                                                     http://1.32.53.97:45188/.i   
1                                                                             https://kld.workout.oystergardener.net/editContent   
2                                                                                            http://178.141.204.195:38244/Mozi.m   
3                                                                          https://github.com/hoter666/8888/blob/main/Banana.exe   
4      http://mail.treeoflifeadventures.com/wp-content/plugins/70d5e28f51c1438d94e3e6dc84b95311/xt/mmd/shell/UMLrjk2KC4fpJg5.exe   
...                                                                                                                          ...   
15234                                                                                       http://berkatamankimsedurduramaz.ml/   
15235                                                                                      https://pklkknj89bygvczvi.com/vvmd54/   
15236                                                                                     https://ngvcfrttgyu512vgv.net/ZgbN19Mx   
15237                                                                     https://ngvcfrttgyu512vgv.net/lander/chrome/_index.php   
15241                                                                           http://status.klopware.space/_Defaultwindows.php   

        status                  last_seen       threat_type  \
0       online  2023-09-15 15:17:09+00:00  payload_delivery   
1      offline  2023-09-15 15:11:08+00:00  payload_delivery   
2      offline  2023-09-15 15:03:04+00:00  payload_delivery   
3       online  2023-09-15 15:04:29+00:00  payload_delivery   
4      offline  2023-09-15 13:56:00+00:00  payload_delivery   
...        ...                        ...               ...   
15234  offline  2023-09-08 19:25:17+00:00            botnet   
15235  offline  2023-09-08 19:25:16+00:00  payload_delivery   
15236  offline  2023-09-08 19:25:16+00:00  payload_delivery   
15237  offline  2023-09-08 19:25:15+00:00  payload_delivery   
15241  offline  2023-09-08 17:55:15+00:00            botnet   

                                                             reference  \
0                                https://urlhaus.abuse.ch/url/2711900/   
1                                https://urlhaus.abuse.ch/url/2711899/   
2                                https://urlhaus.abuse.ch/url/2711898/   
3                                https://urlhaus.abuse.ch/url/2711897/   
4                                https://urlhaus.abuse.ch/url/2711896/   
...                                                                ...   
15234       https://malpedia.caad.fkie.fraunhofer.de/details/apk.alien   
15235  https://malpedia.caad.fkie.fraunhofer.de/details/js.fakeupdates   
15236  https://malpedia.caad.fkie.fraunhofer.de/details/js.fakeupdates   
15237  https://malpedia.caad.fkie.fraunhofer.de/details/js.fakeupdates   
15241       https://malpedia.caad.fkie.fraunhofer.de/details/win.dcrat   

              reporter      source ioc_type      malware  
0       

In [20]:
dup_urls = find_duplicates(urls.ioc)
dup_urls

['https://ilpiccolocampo.it/blog.php',
 'https://imago-dp.com/blog.php',
 'http://eblaghshekayatname.hyperphp.com/sana.apk',
 'https://laurellkhamilton.shubhmishra.com/elegiac',
 'https://www.dropbox.com/e/scl/fi/46jyvsv3hn2k974s5idwc/winscp_ver_6.1.1.msi?rlkey=twfq797tlx5xjlnc9tipnd24x&dl=1',
 'https://winscphub.com/1.php',
 'https://imas.uk.com/blog.php',
 'https://ikhwarn.com/blog.php',
 'https://scauditora.cl/absorbability',
 'https://vocesdelatinoamerica.com/personification',
 'http://5.75.212.216:27015/htdocs.zip',
 'https://heike.teofilius.de/blog.php',
 'https://sahamedalat.x10.bz/Saham%20Man.apk',
 'http://168.119.191.88:9000/htdocs.zip',
 'https://openaico.ir/bot/stream/dl/?q=r6wp3wkS4rU',
 'https://invertirenmercados.com/1.php',
 'https://heldenfutter.de/blog.php',
 'https://heartwoodproperties.com/blog.php',
 'https://gutesherz.or/go.php']

In [21]:
unique_set_ioc = set(urls.ioc)

# Convert the set back to a list if needed
unique_list = list(unique_set_ioc)

unique_urls = pd.DataFrame()
unique_urls['ioc'] =  unique_list
unique_urls

ioc
0                                           http://pr24note.info/1.hta
1                                    http://39.87.104.149:58078/Mozi.m
2                                  http://37.44.238.208/bins/neko.mips
3                                  http://217.182.79.24/bins/sora.arm6
4                                       http://205.251.155.16/sora.x86
...                                                                ...
7620                       http://67.205.175.100/hiddenbin/boatnet.x86
7621                                 http://176.123.1.132:8088/_armv5l
7622  http://45.138.74.83/eramthginseggibruoy/yourbiggestnightmare.arm
7623                                    http://117.63.218.207:49422/.i
7624                               https://123.249.115.56/en_US/all.js

[7625 rows x 1 columns]

### Save values in a folder

In [22]:
unique_urls.to_csv(r'C:\Users\leona\OneDrive\Desktop\Tesi\Pipeline\Datasets\Pipeline\BeforeCollection\urls.csv')

### Summary

--> duplicates found in url

## Summary for ip addresses URL duplicates

In [23]:
# examples

i = 0

df[df['ioc'] == dup_urls[i]]

Unnamed: 0   ID_ENTRY                 first_seen  \
96            96  2711804.0  2023-09-15 06:21:09+00:00   
7106        7106  1163674.0  2023-09-15 06:16:15+00:00   

                                     ioc   status                  last_seen  \
96    https://ilpiccolocampo.it/blog.php  offline  2023-09-15 06:21:09+00:00   
7106  https://ilpiccolocampo.it/blog.php  offline  2023-09-15 06:16:15+00:00   

           threat_type  \
96    payload_delivery   
7106  payload_delivery   

                                                           reference  \
96                             https://urlhaus.abuse.ch/url/2711804/   
7106  https://malpedia.caad.fkie.fraunhofer.de/details/js.gootloader   

         reporter      source ioc_type     malware  
96    Gootloader2    URL Haus      url  GootLoader  
7106  Gootloader2  Threat Fox      url  GootLoader

In [24]:
import random

In [25]:
def create_summary(urls):
    
    summary = pd.DataFrame()
    
    columns = ['url', 'first_seen', 'reporters', 'first_seen_reporter', 'sources' , 'first_seen_source' ,'malwares', 'first_seen_malware', 'times']
    
    row = pd.DataFrame()
    
    for i in range(len(urls)):
                
        tmp_df = df[df['ioc'] == urls[i]]
        
        indexes = tmp_df.index
        
        reporters = []
        sources   = []
        malwares  = []
        
        initial_index = random.choice(indexes)
        
        fs = df.at[initial_index, 'first_seen']
        
        for j in range(len(indexes)):
            
            index = indexes[j]
            
            reporter = df.at[index, 'reporter']
            malware = df.at[index, 'malware']
            first_seen = df.at[index, 'first_seen']

            source = df.at[index, 'source']
            
            sources = list(set(sources + [source]))
            
            r = str(source) + '.' + str(reporter)
            
            reporters = list(set(reporters + [r]))

            malwares = list(set(malwares + [malware]))

            actual_date = datetime.strptime(str(first_seen), '%Y-%m-%d %H:%M:%S%z')
            fs = datetime.strptime(str(fs), '%Y-%m-%d %H:%M:%S%z')
                        
            date_difference = actual_date - fs
            
            if(date_difference.days < 0):
                
                fs = actual_date
                initial_index = index
                       
        u = df.at[initial_index,'ioc']
        r = df.at[initial_index,'reporter'] 
        m = df.at[initial_index,'malware'] 
        s = df.at[initial_index,'source'] 
        d = len(tmp_df)

        row = pd.DataFrame(columns=columns)

        row_values = [u, fs, reporters, r, sources, s, malwares, m, d] 
        row.loc[0] = row_values            
        summary = pd.concat([summary, row]) 
                  
    return summary

In [26]:
summary_urls = create_summary(dup_urls)
summary_urls

url  \
0                                                                                https://ilpiccolocampo.it/blog.php   
0                                                                                     https://imago-dp.com/blog.php   
0                                                                   http://eblaghshekayatname.hyperphp.com/sana.apk   
0                                                                  https://laurellkhamilton.shubhmishra.com/elegiac   
0  https://www.dropbox.com/e/scl/fi/46jyvsv3hn2k974s5idwc/winscp_ver_6.1.1.msi?rlkey=twfq797tlx5xjlnc9tipnd24x&dl=1   
0                                                                                       https://winscphub.com/1.php   
0                                                                                      https://imas.uk.com/blog.php   
0                                                                                      https://ikhwarn.com/blog.php   
0                                                                               https://scauditora.cl/absorbability   
0                                                                  https://vocesdelatinoamerica.com/personification   
0                                                                              http://5.75.212.216:27015/htdocs.zip   
0                                                                               https://heike.teofilius.de/blog.php   
0                                                                        https://sahamedalat.x10.bz/Saham%20Man.apk   
0                                                                             http://168.119.191.88:9000/htdocs.zip   
0                                                                  https://openaico.ir/bot/stream/dl/?q=r6wp3wkS4rU   
0                                                                              https://invertirenmercados.com/1.php   
0                                                                                  https://heldenfutter.de/blog.php   
0                                                                          https://heartwoodproperties.com/blog.php   
0                                                                                       https://gutesherz.or/go.php   

                 first_seen                                       reporters  \
0 2023-09-15 06:16:15+00:00  [URL Haus.Gootloader2, Threat Fox.Gootloader2]   
0 2023-09-15 06:15:47+00:00  [URL Haus.Gootloader2, Threat Fox.Gootloader2]   
0 2023-09-15 06:15:44+00:00    [Threat Fox.onecert_ir, URL Haus.onecert_ir]   
0 2023-09-14 10:30:53+00:00     [URL Haus.JAMESWT_MHT, Threat Fox.Mangusta]   
0 2023-09-14 08:24:27+00:00        [URL Haus.abuse_ch, Threat Fox.abuse_ch]   
0 2023-09-14 08:24:26+00:00        [URL Haus.abuse_ch, Threat Fox.abuse_ch]   
0 2023-09-13 16:43:33+00:00  [URL Haus.Gootloader2, Threat Fox.Gootloader2]   
0 2023-09-13 16:43:33+00:00  [URL Haus.Gootloader2, Threat Fox.Gootloader2]   
0 2023-09-13 12:49:30+00:00       [URL Haus.anonymous, Threat Fox.Mangusta]   
0 2023-09-13 12:49:30+00:00       [URL Haus.anonymous, Threat Fox.Mangusta]   
0 2023-09-13 06:32:11+00:00         [URL Haus.anonymous, Threat Fox.crep1x]   
0 2023-09-13 06:28:28+00:00  [URL Haus.Gootloader2, Threat Fox.Gootloader2]   
0 2023-09-11 06:02:06+00:00    [Threat Fox.onecert_ir, URL Haus.onecert_ir]   
0 2023-09-10 15:22:13+00:00         [URL Haus.anonymous, Threat Fox.crep1x]   
0 2023-09-09 17:37:08+00:00    [Threat Fox.onecert_ir, URL Haus.onecert_ir]   
0 2023-09-09 06:00:00+00:00       [URL Haus.abuse_ch, Threat Fox.monitorsg]   
0 2023-09-08 06:19:13+00:00  [URL Haus.Gootloader2, Threat Fox.Gootloader2]   
0 2023-09-08 06:19:08+00:00  [URL Haus.Gootloader2, Threat Fox.Gootloader2]   
0 2023-09-08 06:19:04+00:00  [URL Haus.Gootloader2, Threat Fox.Gootloader2]   

  first_seen_reporter                 sources first_seen_source  \
0         Gootloader2  [URL Haus, Threat Fox]        Threat Fox   
0         Gootlo

In [27]:
summary_urls.to_csv(r'C:\Users\leona\OneDrive\Desktop\Tesi\Pipeline\Datasets\Pipeline\Summary\Duplicate_urls.csv')

# Ioc Type : 'ip-addresses'

We take both http:// ip_address / somthing and ip addresses declared as ip addresses

Ip Addresses can change multiple times during a certain period, so this cannot be consider as a unique identifier on which we can make some researches over duplication

We could make some analysis on Ip Addresses, the most common reporter and the most common source for that ip address entry. The number of times that a ip address entry is mentioned

In [28]:
ips = df[(df['ioc'].notna()) & (df['ioc_type'] == 'ip:port')]
ips 

Unnamed: 0   ID_ENTRY                 first_seen                 ioc  \
7056         7056  1163856.0  2023-09-15 12:17:38+00:00   146.56.118.82:443   
7057         7057  1163857.0  2023-09-15 12:17:37+00:00  47.94.206.253:8090   
7058         7058  1163858.0  2023-09-15 12:17:37+00:00    80.96.156.43:444   
7059         7059  1163859.0  2023-09-15 12:17:37+00:00  91.193.75.135:7245   
7061         7061  1163861.0  2023-09-15 12:10:22+00:00   172.81.60.60:3467   
...           ...        ...                        ...                 ...   
16594       15580        0.0  2023-08-24 23:29:43+00:00      41.97.47.7:443   
16595       15581        0.0  2023-08-25 01:29:36+00:00    92.9.44.234:2222   
16596       15582        0.0  2023-08-25 10:08:52+00:00  78.152.198.132:443   
16597       15583        0.0  2023-08-25 11:24:40+00:00  113.193.95.229:443   
16598       15584        0.0  2023-08-25 15:24:34+00:00  190.34.24.159:2222   

        status                  last_seen       threat_type  \
7056   offline  2023-09-15 12:17:38+00:00            botnet   
7057   offline  2023-09-15 12:17:37+00:00            botnet   
7058   offline  2023-09-15 12:17:37+00:00            botnet   
7059   offline  2023-09-15 12:17:37+00:00            botnet   
7061   offline  2023-09-15 12:10:22+00:00            botnet   
...        ...                        ...               ...   
16594  offline  2023-08-25 00:00:00+00:00  payload_delivery   
16595  offline  2023-08-25 00:00:00+00:00  payload_delivery   
16596  offline  2023-08-25 00:00:00+00:00  payload_delivery   
16597  offline  2023-08-25 00:00:00+00:00  payload_delivery   
16598  offline  2023-08-25 00:00:00+00:00  payload_delivery   

                                                                reference  \
7056   https://malpedia.caad.fkie.fraunhofer.de/details/win.cobalt_strike   
7057   https://malpedia.caad.fkie.fraunhofer.de/details/win.cobalt_strike   
7058   https://malpedia.caad.fkie.fraunhofer.de/details/win.cobalt_strike   
7059        https://malpedia.caad.fkie.fraunhofer.de/details/win.nanocore   
7061          https://malpedia.caad.fkie.fraunhofer.de/details/win.remcos   
...                                                                   ...   
16594                                      https://feodotracker.abuse.ch/   
16595                                      https://feodotracker.abuse.ch/   
16596                                      https://feodotracker.abuse.ch/   
16597                                      https://feodotracker.abuse.ch/   
16598                                      https://feodotracker.abuse.ch/   

            reporter         source ioc_type       malware  
7056        malpulse     Threat Fox  ip:port  CobaltStrike  
7057        malpulse     Threat Fox  ip:port  CobaltStrike  
7058        malpulse     Threat Fox  ip:port  CobaltStrike  
7059      SarlackLab     Threat Fox  ip:port      NanoCore  
7061        abuse_ch     Threat Fox  ip:port     RemcosRAT  
...              ...            ...      ...           ...  
16594  Feodo Tracker  Feodo Tracker  ip:port        QakBot  
16595  Feodo Tracker  Feodo Tracker  ip:port        QakBot  
16596  Feodo Tracker  Feodo Tracker  ip:port        QakBot  
16597  Feodo Tracker  Feodo Tracker  ip:port        QakBot  
16598  Feodo Tracker  Feodo Tracker  ip:port        QakBot  

[4081 rows x 12 columns]

In [37]:
urls = df[(df['ioc'].notna()) & (df['ioc_type'] == 'url')] 
urls

Unnamed: 0   ID_ENTRY                 first_seen  \
0               0  2711900.0  2023-09-15 15:17:09+00:00   
1               1  2711899.0  2023-09-15 15:11:08+00:00   
2               2  2711898.0  2023-09-15 15:03:04+00:00   
3               3  2711897.0  2023-09-15 13:35:07+00:00   
4               4  2711896.0  2023-09-15 13:33:07+00:00   
...           ...        ...                        ...   
15234       15234  1155704.0  2023-09-08 19:25:17+00:00   
15235       15235  1155710.0  2023-09-08 19:25:16+00:00   
15236       15236  1155711.0  2023-09-08 19:25:16+00:00   
15237       15237  1155712.0  2023-09-08 19:25:15+00:00   
15241       15241  1155706.0  2023-09-08 17:55:15+00:00   

                                                                                                                             ioc  \
0                                                                                                     http://1.32.53.97:45188/.i   
1                                                                             https://kld.workout.oystergardener.net/editContent   
2                                                                                            http://178.141.204.195:38244/Mozi.m   
3                                                                          https://github.com/hoter666/8888/blob/main/Banana.exe   
4      http://mail.treeoflifeadventures.com/wp-content/plugins/70d5e28f51c1438d94e3e6dc84b95311/xt/mmd/shell/UMLrjk2KC4fpJg5.exe   
...                                                                                                                          ...   
15234                                                                                       http://berkatamankimsedurduramaz.ml/   
15235                                                                                      https://pklkknj89bygvczvi.com/vvmd54/   
15236                                                                                     https://ngvcfrttgyu512vgv.net/ZgbN19Mx   
15237                                                                     https://ngvcfrttgyu512vgv.net/lander/chrome/_index.php   
15241                                                                           http://status.klopware.space/_Defaultwindows.php   

        status                  last_seen       threat_type  \
0       online  2023-09-15 15:17:09+00:00  payload_delivery   
1      offline  2023-09-15 15:11:08+00:00  payload_delivery   
2      offline  2023-09-15 15:03:04+00:00  payload_delivery   
3       online  2023-09-15 15:04:29+00:00  payload_delivery   
4      offline  2023-09-15 13:56:00+00:00  payload_delivery   
...        ...                        ...               ...   
15234  offline  2023-09-08 19:25:17+00:00            botnet   
15235  offline  2023-09-08 19:25:16+00:00  payload_delivery   
15236  offline  2023-09-08 19:25:16+00:00  payload_delivery   
15237  offline  2023-09-08 19:25:15+00:00  payload_delivery   
15241  offline  2023-09-08 17:55:15+00:00            botnet   

                                                             reference  \
0                                https://urlhaus.abuse.ch/url/2711900/   
1                                https://urlhaus.abuse.ch/url/2711899/   
2                                https://urlhaus.abuse.ch/url/2711898/   
3                                https://urlhaus.abuse.ch/url/2711897/   
4                                https://urlhaus.abuse.ch/url/2711896/   
...                                                                ...   
15234       https://malpedia.caad.fkie.fraunhofer.de/details/apk.alien   
15235  https://malpedia.caad.fkie.fraunhofer.de/details/js.fakeupdates   
15236  https://malpedia.caad.fkie.fraunhofer.de/details/js.fakeupdates   
15237  https://malpedia.caad.fkie.fraunhofer.de/details/js.fakeupdates   
15241       https://malpedia.caad.fkie.fraunhofer.de/details/win.dcrat   

              reporter      source ioc_type      malware  
0       

In [54]:
import re

def extract_ip_from_url(url):
    # Regular expression pattern to match an IP address
    ip_pattern = r'\b(?:\d{1,3}\.){3}\d{1,3}\b'

    # Find all matches of the IP pattern in the URL
    matches = re.findall(ip_pattern, url)

    # If there are matches, return the first one, otherwise return None
    return matches[0] if matches else None

def check_urls(df):
    
    dataframe = pd.DataFrame()
    
    indexes = df.index
    
    for i in range(len(indexes)):
        
        index = indexes[i]
        
        ioc = df.at[index, 'ioc']
        
        ip = str(extract_ip_from_url(ioc))
        
        print(ip)
                
        if(ip != None):
            
            row = df.iloc[index]
            
            row['ip'] = ip
            
            dataframe = pd.concat([dataframe, row])
            
    
    return dataframe
            
            

In [55]:
dup_urls_ips = check_urls(urls)
dup_urls_ips

1.32.53.97
None
178.141.204.195
None
None
None


C:\Users\leona\AppData\Local\Temp\ipykernel_12084\3302983522.py:33: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  row['ip'] = ip
C:\Users\leona\AppData\Local\Temp\ipykernel_12084\3302983522.py:33: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  row['ip'] = ip
C:\Users\leona\AppData\Local\Temp\ipykernel_12084\3302983522.py:33: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  row['ip'] = ip
C:\Users\leona\AppData\Local\Temp\ipykernel_12084\33

125.228.150.40
None
None
202.178.125.242
None


C:\Users\leona\AppData\Local\Temp\ipykernel_12084\3302983522.py:33: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  row['ip'] = ip
C:\Users\leona\AppData\Local\Temp\ipykernel_12084\3302983522.py:33: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  row['ip'] = ip
C:\Users\leona\AppData\Local\Temp\ipykernel_12084\3302983522.py:33: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  row['ip'] = ip
C:\Users\leona\AppData\Local\Temp\ipykernel_12084\33

None
None
None
None
None
None


...

None
None
None
None
178.62.68.57
167.172.94.190


C:\Users\leona\AppData\Local\Temp\ipykernel_12084\3302983522.py:33: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  row['ip'] = ip
C:\Users\leona\AppData\Local\Temp\ipykernel_12084\3302983522.py:33: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  row['ip'] = ip
C:\Users\leona\AppData\Local\Temp\ipykernel_12084\3302983522.py:33: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  row['ip'] = ip
C:\Users\leona\AppData\Local\Temp\ipykernel_12084\33

62.234.185.105
None
None
None
None
124.70.199.215


C:\Users\leona\AppData\Local\Temp\ipykernel_12084\3302983522.py:33: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  row['ip'] = ip
C:\Users\leona\AppData\Local\Temp\ipykernel_12084\3302983522.py:33: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  row['ip'] = ip
C:\Users\leona\AppData\Local\Temp\ipykernel_12084\3302983522.py:33: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  row['ip'] = ip
C:\Users\leona\AppData\Local\Temp\ipykernel_12084\33

IndexError: single positional indexer is out-of-bounds

In [ ]:
dup_urls['ip'] = 
dup_urls

In [ ]:
ips['ip'] = ips['ioc'].str.split(':').str[0]
ips

In [ ]:
dup_ips = find_duplicates(ips.ip)
len(dup_ips)

In [ ]:
unique_set_ioc = set(ips.ip)

# Convert the set back to a list if needed
unique_list = list(unique_set_ioc)

unique_list

In [ ]:
unique_set_ioc = set(ips.ioc)

# Convert the set back to a list if needed
unique_list = list(unique_set_ioc)

unique_urls = pd.DataFrame()
unique_urls['ioc'] =  unique_list
unique_urls

### Save values in a folder

In [ ]:
unique_urls.to_csv(r'C:\Users\leona\OneDrive\Desktop\Tesi\Pipeline\Datasets\Pipeline\BeforeCollection\urls.csv')

### Summary

--> duplicates found in url

In [ ]:
83.114.60.6

## Summary for ip addresses URL duplicates

In [ ]:
# examples

ips[ips['ip'] == '83.114.60.6']

In [ ]:
def create_summary(urls):
    
    summary = pd.DataFrame()
    
    columns = ['url', 'sources', 'malwares', 'threat_types' , 'most_frequent_malware', 'most_frequent_threat_type' , 'times']
    
    row = pd.DataFrame()
            
    for i in range(len(urls)):
                
        tmp_df = df[df['ioc'] == urls[i]]
        
        indexes = tmp_df.index
        
        reporters = []
        sources   = []
        malwares  = []
        
        initial_index = random.choice(indexes)
        
        fs = df.at[initial_index, 'first_seen']
        
        for j in range(len(indexes)):
            
            index = indexes[j]
            
            reporter = df.at[index, 'reporter']
            malware = df.at[index, 'malware']
            first_seen = df.at[index, 'first_seen']

            source = df.at[index, 'source']
            
            sources = list(set(sources + [source]))
            
            r = str(source) + '.' + str(reporter)
            
            reporters = list(set(reporters + [r]))

            malwares = list(set(malwares + [malware]))

            actual_date = datetime.strptime(str(first_seen), '%Y-%m-%d %H:%M:%S%z')
            fs = datetime.strptime(str(fs), '%Y-%m-%d %H:%M:%S%z')
                        
            date_difference = actual_date - fs
            
            if(date_difference.days < 0):
                
                fs = actual_date
                initial_index = index
                       
        u = df.at[initial_index,'ioc']
        r = df.at[initial_index,'reporter'] 
        m = df.at[initial_index,'malware'] 
        s = df.at[initial_index,'source'] 
        d = len(tmp_df)

        row = pd.DataFrame(columns=columns)

        row_values = [u, fs, reporters, r, sources, s, malwares, m, d] 
        row.loc[0] = row_values            
        summary = pd.concat([summary, row]) 
                  
    return summary

In [ ]:
summary_urls = create_summary(dup_urls)
summary_urls

In [ ]:
summary_urls.to_csv(r'C:\Users\leona\OneDrive\Desktop\Tesi\Pipeline\Datasets\Pipeline\Summary\Duplicate_urls.csv')